# Redshift auto-copy (preview)
This SQL notebook demonstrates how to automate data load from Amazon S3 to Redshift using auto-copy preview feature.
- Automate ingestion from a single data source
- Automate ingestion from multiple data sources

## Pre-requisites

For this demo, you need to create an Amazon Redshift provisioned preview cluster. Refer to creating a preview workgroup or creating a preview cluster documentation for steps
- [Provisioned Preview](https://docs.aws.amazon.com/redshift/latest/mgmt/managing-clusters-console.html#cluster-preview)

## 1.0 Setup the sample tables
The initial step is to create the tables required for this demo
- STORE_SALES
- CAB_SALES_DATA

In [0]:
DROP TABLE IF EXISTS store_sales;
CREATE TABLE IF NOT EXISTS store_sales
(
  ss_sold_date_sk int4 ,            
  ss_sold_time_sk int4 ,     
  ss_item_sk int4 not null ,      
  ss_customer_sk int4 ,           
  ss_cdemo_sk int4 ,              
  ss_hdemo_sk int4 ,         
  ss_addr_sk int4 ,               
  ss_store_sk int4 ,           
  ss_promo_sk int4 ,           
  ss_ticket_number int8 not null,        
  ss_quantity int4 ,           
  ss_wholesale_cost numeric(7,2) ,          
  ss_list_price numeric(7,2) ,              
  ss_sales_price numeric(7,2) ,
  ss_ext_discount_amt numeric(7,2) ,             
  ss_ext_sales_price numeric(7,2) ,              
  ss_ext_wholesale_cost numeric(7,2) ,           
  ss_ext_list_price numeric(7,2) ,               
  ss_ext_tax numeric(7,2) ,                 
  ss_coupon_amt numeric(7,2) , 
  ss_net_paid numeric(7,2) ,   
  ss_net_paid_inc_tax numeric(7,2) ,             
  ss_net_profit numeric(7,2) ,
  primary key (ss_item_sk, ss_ticket_number)
) DISTKEY (ss_item_sk) 
  SORTKEY(ss_sold_date_sk);

  DROP TABLE IF EXISTS cab_sales_data;
CREATE TABLE IF NOT EXISTS cab_sales_data
(
  vendorid                VARCHAR(4),
  pickup_datetime         TIMESTAMP,
  dropoff_datetime        TIMESTAMP,
  store_and_fwd_flag      VARCHAR(1),
  ratecode                INT,
  pickup_longitude        FLOAT4,
  pickup_latitude         FLOAT4,
  dropoff_longitude       FLOAT4,
  dropoff_latitude        FLOAT4,
  passenger_count         INT,
  trip_distance           FLOAT4,
  fare_amount             FLOAT4,
  extra                   FLOAT4,
  mta_tax                 FLOAT4,
  tip_amount              FLOAT4,
  tolls_amount            FLOAT4,
  ehail_fee               FLOAT4,
  improvement_surcharge   FLOAT4,
  total_amount            FLOAT4,
  payment_type            VARCHAR(4),
  trip_type               VARCHAR(4)
)
DISTSTYLE EVEN
SORTKEY (passenger_count,pickup_datetime);

### Validate tables created

In [0]:
Select * from store_sales;
Select * from cab_sales_data;

## 2.0 Automate ingestion from a single data source
You can automate ingestion from a single data source by creating one job and specifying the path to the Amazon S3 objects that contain the data. The S3 object path can reference a set of folders that have the same key prefix.

**2.1. Create COPY job job_store_sales**

NOTE: If your cluster does not have default IAM role then update the IAM_ROLE (line 3) with the IAM role ARN that is attached to your Amazon Redshift cluster. Below copy command creates new copy job called job_stores_sales and loads data for 2 days.

In [0]:
COPY store_sales
FROM 's3://redshift-blogs/amazon-Redshift-auto-copy/store_sales'
IAM_ROLE 'arn:aws:iam::70xxxxx1:role/service-role/AmazonRedshift-CommandsAccessRole-20220416T115923'   /*replace this arn with your role arn*/
gzip delimiter '|' EMPTYASNULL
region 'us-east-1'
JOB CREATE job_store_sales AUTO ON;

### Check the properties of Copy job from system table SYS_COPY_JOB (preview) and Files loaded by copy job from stl_load_commits

In [0]:
--copy job
select * from SYS_COPY_JOB where jon_name = 'job_store_sales'

-- check how many files are load 
SELECT job_id, job_name, data_source, copy_query,filename,status, curtime
FROM sys_copy_job copyjob
JOIN stl_load_commits loadcommit
ON copyjob.job_id = loadcommit.copy_job_id
WHERE job_name = 'job_store_sales'
order by curtime desc;

-- check how many files got loaded
SELECT count(filename)
FROM sys_copy_job copyjob
JOIN stl_load_commits loadcommit
ON copyjob.job_id = loadcommit.copy_job_id
WHERE job_name = 'job_store_sales' and byte_offset >0

### 2.2. Sample the target table
* Daily total sales of transactions 
* Max and Min value for SK key value

NOTE: wait 30-60 seconds before running the query

In [0]:
SELECT ss_sold_date_sk, count(1)
  FROM store_sales
GROUP BY ss_sold_date_sk;

## 3.0 Automate ingestion from multiple data sources
You can automate ingestion from a multiple data sources to a single table by creating one copy job for each data source.

In the following section, two copy jobs are created to handle and monitor automatic ingestion of sales data belonging to different customers - Customer_1 (green cab) and Customer_2 (red_cab).

**3.1. Create COPY job job_green_cab**

NOTE: Update the IAM_ROLE (line 3) with the IAM role ARN that is attached to your Amazon Redshift cluster.

In [0]:
COPY cab_sales_data
FROM 's3://redshift-blogs/amazon-Redshift-auto-copy/Customer_1'
IAM_ROLE 'arn:aws:iam::709512860261:role/service-role/AmazonRedshift-CommandsAccessRole-20220416T115923'
DATEFORMAT 'auto'
IGNOREHEADER 1
DELIMITER ','
IGNOREBLANKLINES
REGION 'us-east-1'
JOB CREATE job_green_cab AUTO ON;

**3.2. Create COPY job job_red_cab**

NOTE: Update the IAM_ROLE (line 3) with the IAM role ARN that is attached to your Amazon Redshift cluster.

In [0]:
COPY cab_sales_data
FROM 's3://redshift-blogs/amazon-Redshift-auto-copy/Customer_2'
IAM_ROLE 'arn:aws:iam::709512860261:role/service-role/AmazonRedshift-CommandsAccessRole-20220416T115923'
DATEFORMAT 'auto'
IGNOREHEADER 1
DELIMITER ','
IGNOREBLANKLINES
REGION 'us-east-1'
JOB CREATE job_red_cab AUTO ON;

**3.3. Let us run a query to get the total number of passengers. Each customer is assigned its own vendorid.**

NOTE: wait 30-60 seconds before running the query

In [0]:
SELECT vendorid,
       sum(passenger_count) as total_passengers 
  FROM cab_sales_data
GROUP BY vendorid;

## 4.0 Monitoring for Copy Jobs
Amazon Redshift provides the following system tables for users to  monitor or troubleshoot copy jobs as needed.

- SYS_COPY_JOB - List all the copy jobs stored in the database
- SYS_LOAD_HISTORY - Shows the aggregate metrics of all the files that have been processed by a copy job
- STL_LOAD_COMMITS - Shows the status and details of each file that was processed by a copy job
- STL_LOAD_ERRORS - Shows the details of file(s) failed to ingest from a copy job

In [0]:
-- Get list of copy jobs
SELECT * 
  FROM sys_copy_job;

-- Get summary of copy jobs
  SELECT c.job_name, l.* 
  FROM sys_load_history l
  INNER JOIN sys_copy_job c ON (l.copy_job_id = c.job_id)
 
 -- Get details of a copy JSONB

 SELECT l.* 
  FROM stl_load_commits l
  INNER JOIN sys_copy_job c ON (l.copy_job_id = c.job_id)
 WHERE c.job_name = 'job_store_sales'  
 ORDER BY l.curtime DESC;

 -- Get exception details

 SELECT l.* 
  FROM stl_load_errors l
  INNER JOIN sys_copy_job c ON (l.copy_job_id = c.job_id)
 WHERE c.job_name = 'job_store_sales';

## 5.0 CLEANUP

Delete the cluster.  Or you can just delete the copy jobs and tables created and retain the cluster if it is used for other purposes.

In [0]:
-- Drop copy jobs

COPY JOB DROP job_store_sales;
COPY JOB DROP job_green_cab;
COPY JOB DROP job_red_cab;

-- Drop the TABLE
DROP TABLE IF EXISTS store_sales;
DROP TABLE IF EXISTS cab_sales_data;